# Geospatial Visualization

## Geojson Data
  
Import Libraries

In [2]:
# Import Libraries
import pandas as pd
import numpy as np
import geopandas as gpd
import folium as flm
import calendar
#  For showing all columns in Pandas
pd.set_option('display.max_columns', None)

# this ignores the depreciation warnings etc
import warnings
warnings.filterwarnings("ignore")

### Create a Dataframe contianing geometry of the Police Station Areas
  
Read in the data and create a DataFrame.

In [3]:
# Read the geoJSON file using geopandas
geo_prov = gpd.read_file(r'../../../data/geodata/sa_provinces.geojson')
geo_prov = geo_prov[["ADM1_ID", "ADM1_EN", "geometry"]] # only select 'COMPNT_NM' (Police Stations) and 'geometry' columns

In [4]:
geo_prov

ADM1_ID        ADM1_EN                                           geometry
0      EC   Eastern Cape  POLYGON ((30.19386 -31.08126, 30.19341 -31.076...
1      FS     Free State  POLYGON ((28.24428 -26.88478, 28.23539 -26.881...
2      GT        Gauteng  POLYGON ((28.24428 -26.88478, 28.24841 -26.884...
3     KZN  KwaZulu-Natal  POLYGON ((30.19386 -31.08126, 30.19399 -31.082...
4     LIM        Limpopo  POLYGON ((31.88383 -23.98459, 31.88092 -23.967...
5      MP     Mpumalanga  POLYGON ((31.88383 -23.98459, 31.85268 -23.986...
6      NW     North West  POLYGON ((28.29816 -25.31037, 28.29823 -25.293...
7      NC   Nothern Cape  POLYGON ((22.63217 -26.12128, 22.62812 -26.123...
8      WC   Western Cape  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...

Fix spelling mistake - 'Nothern Cape' to 'Northern Cape'.

In [5]:
geo_prov['ADM1_EN'] = geo_prov['ADM1_EN'].replace('Nothern Cape','Northern Cape')
geo_prov

ADM1_ID        ADM1_EN                                           geometry
0      EC   Eastern Cape  POLYGON ((30.19386 -31.08126, 30.19341 -31.076...
1      FS     Free State  POLYGON ((28.24428 -26.88478, 28.23539 -26.881...
2      GT        Gauteng  POLYGON ((28.24428 -26.88478, 28.24841 -26.884...
3     KZN  KwaZulu-Natal  POLYGON ((30.19386 -31.08126, 30.19399 -31.082...
4     LIM        Limpopo  POLYGON ((31.88383 -23.98459, 31.88092 -23.967...
5      MP     Mpumalanga  POLYGON ((31.88383 -23.98459, 31.85268 -23.986...
6      NW     North West  POLYGON ((28.29816 -25.31037, 28.29823 -25.293...
7      NC  Northern Cape  POLYGON ((22.63217 -26.12128, 22.62812 -26.123...
8      WC   Western Cape  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...

In [6]:
geo_prov.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 9 entries, 0 to 8
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   ADM1_ID   9 non-null      object  
 1   ADM1_EN   9 non-null      object  
 2   geometry  9 non-null      geometry
dtypes: geometry(1), object(2)
memory usage: 344.0+ bytes


### Create a Dataframe containing the Police Station Crime Data
  
Read in the data and create a DataFrame.

In [7]:
df = pd.read_parquet('../../../data/crime_data_2016_21.parquet')

In [8]:
df

station      province        district  \
0        East London  Eastern Cape  East London Cc   
1        East London  Eastern Cape  East London Cc   
2        East London  Eastern Cape  East London Cc   
3        East London  Eastern Cape  East London Cc   
4        East London  Eastern Cape  East London Cc   
...              ...           ...             ...   
3665371  Protea Glen       Gauteng  Soweto West Cc   
3665372  Protea Glen       Gauteng  Soweto West Cc   
3665373  Protea Glen       Gauteng  Soweto West Cc   
3665374  Protea Glen       Gauteng  Soweto West Cc   
3665375  Protea Glen       Gauteng  Soweto West Cc   

                              crime_category    date  number_of_crimes  \
0        17 Community Reported Serious Crime  Jan-16               470   
1        17 Community Reported Serious Crime  Feb-16               411   
2        17 Community Reported Serious Crime  Mar-16               477   
3        17 Community Reported Serious Crime  Jan-17               476   
4        17 Community Reported Serious Crime  Feb-17               427   
...                                      ...     ...               ...   
3665371                      Truck hijacking  Nov-20                 0   
3665372                      Truck hijacking  Dec-20                 0   
3665373                      Truck hijacking  Oct-21                 0   
3665374                      Truck hijacking  Nov-21                 0   
3665375                      Truck hijacking  Dec-21                 0   

         latitude  longitude  
0       -33.02058   27.90288  
1       -33.02058   27.90288  
2       -33.02058   27.90288  
3       -33.02058   27.90288  
4       -33.02058   27.90288  
...           ...        ...  
3665371 -26.27697   27.83896  
3665372 -26.27697   27.83896  
3665373 -26.27697   27.83896  
3665374 -26.27697   27.83896  
3665375 -26.27697   27.83896  

[3665376 rows x 8 columns]

Lets get the geometric district names

In [9]:
df2 = pd.read_csv('district_municipals.csv')
df2  = pd.DataFrame(df2[['district', 'main_district']])
df2

district main_district
0      Mount Ayliff Cc    Alfred Nzo
1           Amajuba Cc       Amajuba
2       Butterworth Cc      Amathole
3             Alice Cc      Amathole
4        Rustenburg Cc      Bojanala
..                 ...           ...
117      Trompsburg Cc       Xhariep
118       Zf Mgcawu Cc    Z F Mgcawu
119  King Cetshwayo Cc     Uthungulu
120          Ilembe Cc        iLembe
121        Zululand Cc      Zululand

[122 rows x 2 columns]

Lets merge with the DataFrame.

In [10]:
df = df.merge(df2, on='district', how='left')
df

station      province        district  \
0        East London  Eastern Cape  East London Cc   
1        East London  Eastern Cape  East London Cc   
2        East London  Eastern Cape  East London Cc   
3        East London  Eastern Cape  East London Cc   
4        East London  Eastern Cape  East London Cc   
...              ...           ...             ...   
3665371  Protea Glen       Gauteng  Soweto West Cc   
3665372  Protea Glen       Gauteng  Soweto West Cc   
3665373  Protea Glen       Gauteng  Soweto West Cc   
3665374  Protea Glen       Gauteng  Soweto West Cc   
3665375  Protea Glen       Gauteng  Soweto West Cc   

                              crime_category    date  number_of_crimes  \
0        17 Community Reported Serious Crime  Jan-16               470   
1        17 Community Reported Serious Crime  Feb-16               411   
2        17 Community Reported Serious Crime  Mar-16               477   
3        17 Community Reported Serious Crime  Jan-17               476   
4        17 Community Reported Serious Crime  Feb-17               427   
...                                      ...     ...               ...   
3665371                      Truck hijacking  Nov-20                 0   
3665372                      Truck hijacking  Dec-20                 0   
3665373                      Truck hijacking  Oct-21                 0   
3665374                      Truck hijacking  Nov-21                 0   
3665375                      Truck hijacking  Dec-21                 0   

         latitude  longitude         main_district  
0       -33.02058   27.90288          Buffalo City  
1       -33.02058   27.90288          Buffalo City  
2       -33.02058   27.90288          Buffalo City  
3       -33.02058   27.90288          Buffalo City  
4       -33.02058   27.90288          Buffalo City  
...           ...        ...                   ...  
3665371 -26.27697   27.83896  City of Johannesburg  
3665372 -26.27697   27.83896  City of Johannesburg  
3665373 -26.27697   27.83896  City of Johannesburg  
3665374 -26.27697   27.83896  City of Johannesburg  
3665375 -26.27697   27.83896  City of Johannesburg  

[3665376 rows x 9 columns]

Lets do a bit of housekeeping to tidy things up.

In [11]:
df.columns

Index(['station', 'province', 'district', 'crime_category', 'date',
       'number_of_crimes', 'latitude', 'longitude', 'main_district'],
      dtype='object')

In [12]:
df = df[
    ['station', 'district', 'main_district', 'province', 'date',
     'crime_category', 'number_of_crimes', 'latitude', 'longitude',]]
df.head(1)

station        district main_district      province    date  \
0  East London  East London Cc  Buffalo City  Eastern Cape  Jan-16   

                        crime_category  number_of_crimes  latitude  longitude  
0  17 Community Reported Serious Crime               470 -33.02058   27.90288

In [13]:
df.rename(columns = {'district':'municipality', 'main_district': 'district'}, inplace = True)
df.head(1)

station    municipality      district      province    date  \
0  East London  East London Cc  Buffalo City  Eastern Cape  Jan-16   

                        crime_category  number_of_crimes  latitude  longitude  
0  17 Community Reported Serious Crime               470 -33.02058   27.90288

Change the format of 'Kwazulu/Natal' to match 'Kwazulu-Natal'.

In [14]:
df['province'] = df['province'].replace('Kwazulu/Natal','KwaZulu-Natal')
df.sample(10)

station        municipality             district       province  \
3010021  Richmond(C)   Pixley Ka Seme Cc       Pixley ka Seme  Northern Cape   
2951065     Hopetown   Pixley Ka Seme Cc       Pixley ka Seme  Northern Cape   
2382084    Barberton          Pienaar Cc   Thabo Mofutsanyane     Mpumalanga   
1471354     Madadeni          Amajuba Cc              Amajuba  KwaZulu-Natal   
3496926    Piketberg       Vredenburg Cc           West Coast   Western Cape   
1415169    Boipatong         Sedibeng Cc             Sedibeng        Gauteng   
2698997     Itsoseng         Mahikeng Cc  Ngaka Modiri Molema     North West   
2030570      Seshego          Seshego Cc            Capricorn        Limpopo   
3333707     Philippi  Mitchells Plain Cc    City of Cape Town   Western Cape   
3006246    Colesberg   Pixley Ka Seme Cc       Pixley ka Seme  Northern Cape   

           date                                     crime_category  \
3010021  May-18                                         Kidnapping   
2951065  Nov-16  Assault with the intent to inflict grievous bo...   
2382084  Jan-16                                               Rape   
1471354  Aug-21                         Robbery of cash in transit   
3496926  Jan-20                                     Common robbery   
1415169  Oct-19                                    Sexual offences   
2698997  Mar-17                                    Sexual offences   
2030570  Mar-18  Sexual offences detected as a result of police...   
3333707  Sep-21                   Burglary at residential premises   
3006246  Jan-20                         Robbery of cash in transit   

         number_of_crimes  latitude  longitude  
3010021                 0 -31.41508   23.94401  
2951065                 7 -29.61956   24.08728  
2382084                11 -25.79074   31.05178  
1471354                 0 -27.76200   30.02664  
3496926                 0 -32.90627   18.75449  
1415169                 0 -26.66959   27.84344  
2698997                 5 -26.08725   25.88043  
2030570                 0 -23.85429   29.38227  
3333707                 8 -34.00107   18.54054  
3006246                 0 -30.71970   25.09446

Lets check the shape of the dataframe and the length of 'province'.

In [15]:
len(df['province'].unique())

9

Quick check of the shape confirms all is good.

In [16]:
geo_prov.shape

(9, 3)

Lets check the column names.

In [17]:
geo_prov.columns

Index(['ADM1_ID', 'ADM1_EN', 'geometry'], dtype='object')

We will renmane the column 'ADM1_EN' to 'province', and 'geometry' to 'geometry_prov'

In [18]:
geo_prov.rename(columns = {'ADM1_EN':'province', 'geometry': 'geometry_prov'}, inplace = True)
geo_prov

ADM1_ID       province                                      geometry_prov
0      EC   Eastern Cape  POLYGON ((30.19386 -31.08126, 30.19341 -31.076...
1      FS     Free State  POLYGON ((28.24428 -26.88478, 28.23539 -26.881...
2      GT        Gauteng  POLYGON ((28.24428 -26.88478, 28.24841 -26.884...
3     KZN  KwaZulu-Natal  POLYGON ((30.19386 -31.08126, 30.19399 -31.082...
4     LIM        Limpopo  POLYGON ((31.88383 -23.98459, 31.88092 -23.967...
5      MP     Mpumalanga  POLYGON ((31.88383 -23.98459, 31.85268 -23.986...
6      NW     North West  POLYGON ((28.29816 -25.31037, 28.29823 -25.293...
7      NC  Northern Cape  POLYGON ((22.63217 -26.12128, 22.62812 -26.123...
8      WC   Western Cape  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...

The 'geo_prov' data matches the 'df' 'DataFrame'

Now we can check the data types.

In [19]:
geo_prov.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 9 entries, 0 to 8
Data columns (total 3 columns):
 #   Column         Non-Null Count  Dtype   
---  ------         --------------  -----   
 0   ADM1_ID        9 non-null      object  
 1   province       9 non-null      object  
 2   geometry_prov  9 non-null      geometry
dtypes: geometry(1), object(2)
memory usage: 344.0+ bytes


In [20]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3665376 entries, 0 to 3665375
Data columns (total 9 columns):
 #   Column            Dtype  
---  ------            -----  
 0   station           object 
 1   municipality      object 
 2   district          object 
 3   province          object 
 4   date              object 
 5   crime_category    object 
 6   number_of_crimes  int32  
 7   latitude          float64
 8   longitude         float64
dtypes: float64(2), int32(1), object(6)
memory usage: 265.7+ MB


## Merge the DataFrames

Lets create a new DataFrame of the merged DataFrames.

In [21]:
geospatial_main = geo_prov.merge(df, on=['province'], how='left')

In [22]:
geospatial_main

ADM1_ID      province  \
0            EC  Eastern Cape   
1            EC  Eastern Cape   
2            EC  Eastern Cape   
3            EC  Eastern Cape   
4            EC  Eastern Cape   
...         ...           ...   
3665371      WC  Western Cape   
3665372      WC  Western Cape   
3665373      WC  Western Cape   
3665374      WC  Western Cape   
3665375      WC  Western Cape   

                                             geometry_prov  \
0        POLYGON ((30.19386 -31.08126, 30.19341 -31.076...   
1        POLYGON ((30.19386 -31.08126, 30.19341 -31.076...   
2        POLYGON ((30.19386 -31.08126, 30.19341 -31.076...   
3        POLYGON ((30.19386 -31.08126, 30.19341 -31.076...   
4        POLYGON ((30.19386 -31.08126, 30.19341 -31.076...   
...                                                    ...   
3665371  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...   
3665372  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...   
3665373  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...   
3665374  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...   
3665375  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...   

                    station    municipality           district    date  \
0               East London  East London Cc       Buffalo City  Jan-16   
1               East London  East London Cc       Buffalo City  Feb-16   
2               East London  East London Cc       Buffalo City  Mar-16   
3               East London  East London Cc       Buffalo City  Jan-17   
4               East London  East London Cc       Buffalo City  Feb-17   
...                     ...             ...                ...     ...   
3665371  Int Airport C Town   East Metropol  City of Cape Town  Nov-20   
3665372  Int Airport C Town   East Metropol  City of Cape Town  Dec-20   
3665373  Int Airport C Town   East Metropol  City of Cape Town  Oct-21   
3665374  Int Airport C Town   East Metropol  City of Cape Town  Nov-21   
3665375  Int Airport C Town   East Metropol  City of Cape Town  Dec-21   

                              crime_category  number_of_crimes  latitude  \
0        17 Community Reported Serious Crime               470 -33.02058   
1        17 Community Reported Serious Crime               411 -33.02058   
2        17 Community Reported Serious Crime               477 -33.02058   
3        17 Community Reported Serious Crime               476 -33.02058   
4        17 Community Reported Serious Crime               427 -33.02058   
...                                      ...               ...       ...   
3665371                      Truck hijacking                 0 -33.97146   
3665372                      Truck hijacking                 0 -33.97146   
3665373                      Truck hijacking                 0 -33.97146   
3665374                      Truck hijacking                 0 -33.97146   
3665375                      Truck hijacking                 0 -33.97146   

         longitude  
0         27.90288  
1         27.90288  
2         27.90288  
3         27.90288  
4         27.90288  
...            ...  
3665371   18.59990  
3665372   18.59990  
3665373   18.59990  
3665374   18.59990  
3665375   18.59990  

[3665376 rows x 11 columns]

Lets create a matching 'prov_id' from 'ADM1_ID'.

In [23]:
geospatial_main['prov_id'] = geospatial_main.loc[:, 'ADM1_ID']

In [24]:
geospatial_main.sample(2)

ADM1_ID       province  \
2898873      NC  Northern Cape   
53050        EC   Eastern Cape   

                                             geometry_prov        station  \
2898873  POLYGON ((22.63217 -26.12128, 22.62812 -26.123...      Galeshewe   
53050    POLYGON ((30.19386 -31.08126, 30.19341 -31.076...  Graaff-Reinet   

             municipality       district    date  \
2898873  Frances Baard Cc  Frances Baard  Jan-19   
53050    Graaff-Reinet Cc         Cacadu  Aug-17   

                               crime_category  number_of_crimes  latitude  \
2898873  Burglary at non-residential premises                10 -28.71051   
53050                         Truck hijacking                 0 -32.25286   

         longitude prov_id  
2898873   24.74277      NC  
53050     24.53989      EC

Lets change the date to 'datetime'.

In [25]:
geospatial_main['date'] = pd.to_datetime(geospatial_main['date'], format='%b-%y')

Quick check.

In [26]:
geospatial_main.head(1)

ADM1_ID      province                                      geometry_prov  \
0      EC  Eastern Cape  POLYGON ((30.19386 -31.08126, 30.19341 -31.076...   

       station    municipality      district       date  \
0  East London  East London Cc  Buffalo City 2016-01-01   

                        crime_category  number_of_crimes  latitude  longitude  \
0  17 Community Reported Serious Crime               470 -33.02058   27.90288   

  prov_id  
0      EC

### Create Month and Year columns

In [27]:
geospatial_main['month'] = geospatial_main['date'].apply(lambda x: x.month)
geospatial_main['month'] = geospatial_main['month'].apply(lambda x: calendar.month_abbr[x])
geospatial_main['year'] = geospatial_main['date'].apply(lambda x: x.year)
geospatial_main.head(1)

ADM1_ID      province                                      geometry_prov  \
0      EC  Eastern Cape  POLYGON ((30.19386 -31.08126, 30.19341 -31.076...   

       station    municipality      district       date  \
0  East London  East London Cc  Buffalo City 2016-01-01   

                        crime_category  number_of_crimes  latitude  longitude  \
0  17 Community Reported Serious Crime               470 -33.02058   27.90288   

  prov_id month  year  
0      EC   Jan  2016

Reorder columns

In [28]:

geospatial_main = geospatial_main[
    ['station', 'district', 'province', 'prov_id',
     'crime_category', 'date', 'month', 'year',
     'number_of_crimes', 'latitude', 'longitude',
     'ADM1_ID', 'geometry_prov']]
geospatial_main.head(1)

station      district      province prov_id  \
0  East London  Buffalo City  Eastern Cape      EC   

                        crime_category       date month  year  \
0  17 Community Reported Serious Crime 2016-01-01   Jan  2016   

   number_of_crimes  latitude  longitude ADM1_ID  \
0               470 -33.02058   27.90288      EC   

                                       geometry_prov  
0  POLYGON ((30.19386 -31.08126, 30.19341 -31.076...

In [29]:
geospatial_main['year'].info()

<class 'pandas.core.series.Series'>
Int64Index: 3665376 entries, 0 to 3665375
Series name: year
Non-Null Count    Dtype
--------------    -----
3665376 non-null  int64
dtypes: int64(1)
memory usage: 55.9 MB


Lets change the year to a string.

In [30]:
geospatial_main['year'] = geospatial_main['year'].map(str)

In [31]:
geospatial_main['year'].info()

<class 'pandas.core.series.Series'>
Int64Index: 3665376 entries, 0 to 3665375
Series name: year
Non-Null Count    Dtype 
--------------    ----- 
3665376 non-null  object
dtypes: object(1)
memory usage: 55.9+ MB


## Mapping
Lets create a dataframe for the Folium map.

### Yearly Data

In [32]:
map1 = geospatial_main.groupby(['prov_id', 'province', 'year', 'ADM1_ID'], as_index=False).agg({'number_of_crimes': 'sum'})
map1.head()

prov_id      province  year ADM1_ID  number_of_crimes
0      EC  Eastern Cape  2016      EC            587452
1      EC  Eastern Cape  2017      EC            570766
2      EC  Eastern Cape  2018      EC            578181
3      EC  Eastern Cape  2019      EC            579301
4      EC  Eastern Cape  2020      EC            500245

In [33]:
map1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 54 entries, 0 to 53
Data columns (total 5 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   prov_id           54 non-null     object
 1   province          54 non-null     object
 2   year              54 non-null     object
 3   ADM1_ID           54 non-null     object
 4   number_of_crimes  54 non-null     int32 
dtypes: int32(1), object(4)
memory usage: 2.0+ KB


In [34]:
geo_prov

ADM1_ID       province                                      geometry_prov
0      EC   Eastern Cape  POLYGON ((30.19386 -31.08126, 30.19341 -31.076...
1      FS     Free State  POLYGON ((28.24428 -26.88478, 28.23539 -26.881...
2      GT        Gauteng  POLYGON ((28.24428 -26.88478, 28.24841 -26.884...
3     KZN  KwaZulu-Natal  POLYGON ((30.19386 -31.08126, 30.19399 -31.082...
4     LIM        Limpopo  POLYGON ((31.88383 -23.98459, 31.88092 -23.967...
5      MP     Mpumalanga  POLYGON ((31.88383 -23.98459, 31.85268 -23.986...
6      NW     North West  POLYGON ((28.29816 -25.31037, 28.29823 -25.293...
7      NC  Northern Cape  POLYGON ((22.63217 -26.12128, 22.62812 -26.123...
8      WC   Western Cape  MULTIPOLYGON (((19.41807 -34.68668, 19.41489 -...

Merge Geometry into DataFrame.

In [35]:
mapped_prov = pd.merge(map1, geo_prov, on=['ADM1_ID'], how='left')
mapped_prov = mapped_prov[['prov_id', 'province_x', 'year', 'ADM1_ID', 'number_of_crimes', 'geometry_prov']]
mapped_prov.rename(columns = {'province_x':'province'}, inplace = True)
mapped_prov

prov_id       province  year ADM1_ID  number_of_crimes  \
0       EC   Eastern Cape  2016      EC            587452   
1       EC   Eastern Cape  2017      EC            570766   
2       EC   Eastern Cape  2018      EC            578181   
3       EC   Eastern Cape  2019      EC            579301   
4       EC   Eastern Cape  2020      EC            500245   
5       EC   Eastern Cape  2021      EC            516424   
6       FS     Free State  2016      FS            340704   
7       FS     Free State  2017      FS            320926   
8       FS     Free State  2018      FS            318520   
9       FS     Free State  2019      FS            305610   
10      FS     Free State  2020      FS            264900   
11      FS     Free State  2021      FS            281801   
12      GT        Gauteng  2016      GT           1792840   
13      GT        Gauteng  2017      GT           1728982   
14      GT        Gauteng  2018      GT           1685550   
15      GT        Gauteng  2019      GT           1642670   
16      GT        Gauteng  2020      GT           1338797   
17      GT        Gauteng  2021      GT           1358913   
18     KZN  KwaZulu-Natal  2016     KZN            970621   
19     KZN  KwaZulu-Natal  2017     KZN            956128   
20     KZN  KwaZulu-Natal  2018     KZN            942413   
21     KZN  KwaZulu-Natal  2019     KZN            918386   
22     KZN  KwaZulu-Natal  2020     KZN            781567   
23     KZN  KwaZulu-Natal  2021     KZN            808085   
24     LIM        Limpopo  2016     LIM            372525   
25     LIM        Limpopo  2017     LIM            352342   
26     LIM        Limpopo  2018     LIM            357951   
27     LIM        Limpopo  2019     LIM            333571   
28     LIM        Limpopo  2020     LIM            292483   
29     LIM        Limpopo  2021     LIM            303363   
30      MP     Mpumalanga  2016      MP            361723   
31      MP     Mpumalanga  2017      MP            352293   
32      MP     Mpumalanga  2018      MP            347426   
33      MP     Mpumalanga  2019      MP            345784   
34      MP     Mpumalanga  2020      MP            293987   
35      MP     Mpumalanga  2021      MP            297738   
36      NC  Northern Cape  2016      NC            149147   
37      NC  Northern Cape  2017      NC            146641   
38      NC  Northern Cape  2018      NC            144456   
39      NC  Northern Cape  2019      NC            144045   
40      NC  Northern Cape  2020      NC            129022   
41      NC  Northern Cape  2021      NC            127991   
42      NW     North West  2016      NW            336612   
43      NW     North West  2017      NW            333283   
44      NW     North West  2018      NW            339708   
45      NW     North West  2019      NW            321383   
46      NW     North West  2020      NW            273784   
47      NW     North West  2021      NW            287004   
48      WC   Western Cape  2016      WC           1387823   
49      WC   Western Cape  2017      WC           1340452   
50      WC   Western Cape  2018      WC           1276481   
51      WC   Western Cape  2019      WC           1177208   
52      WC   Western Cape  2020      WC            953356   
53      WC   Western Cape  2021      WC            964241   

                                        geometry_prov  
0   POLYGON ((30.19386 -31.08126, 30.19341 -31.076...  
1   POLYGON ((30.19386 -31.08126, 30.19341 -31.076...  
2   POLYGON ((30.19386 -31.08126, 30.19341 -31.076...  
3   POLYGON ((30.19386 -31.08126, 30.19341 -31.076...  
4   POLYGON ((30.19386 -31.08126, 30.19341 -31.076...  
5   POLYGON ((30.19386 -31.08126, 30.19341 -31.076...  
6   POLYGON ((28.24428 -26.88478, 28.23539 -26.881...  
7   POLYGON ((28.24428 -26.88478, 28.23539 -26.881...  
8   POLYGON ((28.24428 -26.88478, 28.23539 -26.881...  
9   POLYGON ((28.24428 -26.88478, 28.23539 -26.881...  
10  POLYGON ((28.24428 -26.8847

Convert to a GeoPandas DatFrame.

In [36]:
mapped_prov = gpd.GeoDataFrame(mapped_prov, geometry='geometry_prov')
type(mapped_prov)

geopandas.geodataframe.GeoDataFrame

In [50]:
sa_map = flm.Map(location=[-28.343, 25.862], zoom_start=6, scrollWheelZoom=False, overlay=False, tiles=None)

flm.TileLayer('openstreetmap', name="Light Map", control=False).add_to(sa_map)

ft_2016 = mapped_prov[mapped_prov['year'] == '2016']
ft_2017 = mapped_prov[mapped_prov['year'] == '2017']
ft_2018 = mapped_prov[mapped_prov['year'] == '2018']
ft_2019 = mapped_prov[mapped_prov['year'] == '2019']
ft_2020 = mapped_prov[mapped_prov['year'] == '2020']
ft_2021 = mapped_prov[mapped_prov['year'] == '2021']

fg0 = flm.FeatureGroup(name='ft_2016',overlay=False).add_to(sa_map)
fg1 = flm.FeatureGroup(name='ft_2017',overlay=False).add_to(sa_map)
fg2 = flm.FeatureGroup(name='ft_2018',overlay=False).add_to(sa_map)
fg3 = flm.FeatureGroup(name='ft_2019',overlay=False).add_to(sa_map)
fg4 = flm.FeatureGroup(name='ft_2020',overlay=False).add_to(sa_map)
fg5 = flm.FeatureGroup(name='ft_2021',overlay=False).add_to(sa_map)

fs = [fg0, fg1, fg2, fg3, fg4, fg5]
year_data = [ft_2016, ft_2017, ft_2018, ft_2019, ft_2020, ft_2021]

custom_scale = (mapped_prov['number_of_crimes'].quantile((0,0.2,0.4,0.6,0.7,0.8,0.9,1))).tolist()

for i in range(len(year_data)):
    crimes_per_year = flm.Choropleth(
                geo_data=r'../../../data/geodata/sa_provinces.geojson',
                data=year_data[i],
                columns=['prov_id', 'number_of_crimes'],
                key_on='feature.properties.ADM1_ID',
                threshold_scale=custom_scale,
                fill_color='YlGnBu',
                nan_fill_color="blue",
                fill_opacity=0.5,
                line_opacity=0.2,
                legend_name='Number of Crimes',
                highlight=True,
                reset=True,
                line_color='black').geojson.add_to(fs[i])

    # Add customized tooltips to the map
    flm.features.GeoJson(
                        data = year_data[i],
                        name='Crimes Per Year',
                        smooth_factor=2,
                        style_function=lambda x: {'color':'black','fillColor':'transparent','weight':0.5},
                        tooltip=flm.features.GeoJsonTooltip(
                            fields=['province',
                                    'year',
                                    'number_of_crimes',
                                ],
                            aliases=["Province:",
                                    "Year",
                                    "Number of Crimes:",
                                    ],
                            localize=True,
                            sticky=False,
                            labels=True,
                            style="""
                                background-color: #F0EFEF;
                                border: 2px solid black;
                                border-radius: 3px;
                                box-shadow: 3px;
                            """,
                            max_width=800,),
                                highlight_function=lambda x: {'weight':3,'fillColor':'grey'},
                            ).add_to(crimes_per_year)

flm.TileLayer('openstreetmap', overlay=True, name="light mode").add_to(sa_map)
flm.LayerControl(collapsed=False).add_to(sa_map)
sa_map.save('SA_Yearly_Crime_by_Province.html')
sa_map